In [602]:
import torch
import os
import numpy as np

import gen_utils as gu
import trimesh
import open3d as o3d
from dataset.common import normal_redirect
import augmentator as aug

In [603]:
Y_AXIS_MAX = 33.15232091532151
Y_AXIS_MIN = -36.9843781139949

In [604]:
aug_obj = aug.Augmentator([aug.Scaling([0.85, 1.15]), aug.Rotation([-180,180], 'rand'), aug.Translation([-0.2, 0.2])])

In [605]:
obj_path = "../datasets/3D_scans_per_patient_obj_files/0KPHM46Q/0KPHM46Q_lower.obj"
# obj_path = "./test_input/Case_40_lower(Antagonist).obj"

In [606]:
tri_mesh_loaded_mesh = trimesh.load_mesh(obj_path, process=False)
vertex_ls = np.array(tri_mesh_loaded_mesh.vertices)
tri_ls = np.array(tri_mesh_loaded_mesh.faces)+1

In [607]:
tri_mesh_loaded_mesh

<trimesh.Trimesh(vertices.shape=(104948, 3), faces.shape=(209802, 3))>

In [608]:
vertex_ls.shape, tri_ls.shape

((104948, 3), (209802, 3))

In [609]:
vertex_ls

array([[-27.35175359,   4.30612546, -96.4654621 ],
       [ 11.87912268, -17.17582173, -94.63727699],
       [-12.77179623, -14.95858494, -91.12811049],
       ...,
       [-16.1351385 , -10.54485817, -93.22231178],
       [-21.47338842,  19.28204543, -88.9329386 ],
       [ 23.49504667,  15.04802914, -89.48448672]])

In [610]:
tri_ls

array([[  1502,    540,    862],
       [  2386,   1389,    567],
       [  2386,   1139,   1389],
       ...,
       [104948,  69590,  48990],
       [ 18110,  97134, 104948],
       [104948,  97134,  69590]])

In [611]:
mesh = o3d.geometry.TriangleMesh()
mesh.vertices = o3d.utility.Vector3dVector(vertex_ls)
mesh.triangles = o3d.utility.Vector3iVector(np.array(tri_ls)-1)
mesh.compute_vertex_normals()
norms = np.array(mesh.vertex_normals)
vertex_ls = np.array(vertex_ls)

In [612]:
norms.shape, vertex_ls.shape

((104948, 3), (104948, 3))

In [613]:
# vertex_ls -= np.mean(vertex_ls, axis=0)
vertex_ls = vertex_ls / np.max(np.abs(vertex_ls))
# vertex_ls = ((vertex_ls-Y_AXIS_MIN)/(Y_AXIS_MAX - Y_AXIS_MIN))*2-1

In [614]:
src_normals = normal_redirect(vertex_ls, norms, view_point=np.array([0., 0., 0.]))
src_normals

array([[-0.53203186, -0.54375409,  0.64905593],
       [-0.25050072,  0.9667127 ,  0.05211474],
       [-0.18712704, -0.2255675 ,  0.95608722],
       ...,
       [ 0.53299509,  0.84193797, -0.08400406],
       [-0.02443996, -0.67504601,  0.73737071],
       [-0.68866542, -0.08315891,  0.72029476]])

In [615]:
vertex_normals = np.concatenate([vertex_ls, src_normals], axis=-1)
vertex_normals.shape

(104948, 6)

In [616]:
# aug_obj.reload_vals()
# src_pcd = aug_obj.run(np.concatenate([vertex_ls, src_normals], axis=-1))
# src_pcd.shape

In [617]:
'''Sampling'''
# vertex_normals = gu.resample_pcd([vertex_normals], 24000, "fps")[0]
# vertex_normals.shape

'Sampling'

In [618]:
# tri_mesh = trimesh.Trimesh(vertices=vertex_ls[:, :3], faces=mesh.triangles)
tri_mesh = trimesh.Trimesh(vertices=vertex_normals[:, :3])
# tri_mesh = trimesh.Trimesh(vertices=mesh.vertices, faces=mesh.triangles)

In [619]:
tri_mesh

<trimesh.Trimesh(vertices.shape=(104948, 3), faces.shape=(0, 3))>

In [620]:
tri_mesh.vertices

TrackedArray([[-0.22616347,  0.03560606, -0.79764407],
              [ 0.09822491, -0.14202174, -0.78252735],
              [-0.10560616, -0.12368807, -0.7535111 ],
              ...,
              [-0.13341664, -0.08719228, -0.77082743],
              [-0.17755703,  0.15943747, -0.73535988],
              [ 0.19427352,  0.12442765, -0.73992047]])

In [621]:
tri_mesh.faces

array([], shape=(0, 3), dtype=int64)

In [622]:
tri_points = trimesh.points.PointCloud(vertex_normals[:, :3])
tri_points

<trimesh.PointCloud(vertices.shape=(104948, 3))>

In [623]:
tri_points.export("test_osstem_2.obj")

'# https://github.com/mikedh/trimesh\nv -0.22616347 0.03560606 -0.79764407\nv 0.09822491 -0.14202174 -0.78252735\nv -0.10560616 -0.12368807 -0.75351110\nv 0.00248321 -0.12637459 -0.72926605\nv 0.03790373 -0.10579558 -0.75100520\nv 0.24830476 0.17506995 -0.75860479\nv -0.00916285 -0.12054190 -0.73492997\nv 0.15943195 0.14949277 -0.76970876\nv 0.20282448 0.05623561 -0.75910633\nv 0.20964999 0.22983329 -0.73550697\nv 0.12794405 -0.02034840 -0.73343514\nv -0.15598949 0.06429690 -0.73174631\nv 0.16209595 0.12211212 -0.74707554\nv 0.13040088 -0.13101754 -0.76906061\nv -0.14284388 0.12400517 -0.73619149\nv 0.19492519 0.19724164 -0.75146750\nv -0.15663594 -0.05895907 -0.76544924\nv -0.15251318 -0.05577540 -0.75703678\nv -0.00603476 -0.16532751 -0.72873564\nv 0.11102260 -0.07847720 -0.70781347\nv 0.23703217 0.03119960 -0.81369435\nv 0.03986663 -0.16153555 -0.78807298\nv 0.08144511 -0.11095617 -0.71910642\nv 0.18956791 0.18750186 -0.75159035\nv 0.02088119 -0.12671483 -0.73077138\nv 0.01921492 -0

In [398]:
tri_mesh.export("test_1.obj")

'# https://github.com/mikedh/trimesh\nv -27.35175359 4.30612546 -96.46546210\nv 41.28457596 23.22864762 -119.54257972\nv 15.09168003 -25.61508332 -111.25613813\nv -1.54148823 31.47422966 -119.82268759\nv 17.96545095 10.81129866 -88.81451091\nv -38.22021232 29.51106211 -118.64607719\nv -3.62652927 -17.60879486 -82.53113049\nv -21.37372156 -24.67625996 -110.54003629\nv -19.60877071 34.55611568 -93.21671685\nv 31.32716489 37.19372378 -95.42053899\nv 30.81298752 -2.74926023 -115.21721118\nv -3.55562492 8.55833688 -101.34257205\nv -44.57445110 21.74354744 -96.79464392\nv 18.19312871 -12.95604231 -91.08183943\nv 20.71271704 32.66536797 -120.53653664\nv -39.22336620 7.90261016 -115.23074563\nv 36.75268681 13.73447316 -102.94044250\nv -16.03770022 -11.63808236 -96.44650277\nv 11.54974396 27.00799003 -104.59601709\nv -30.36177736 -8.38603704 -112.88402850\nv -20.22451732 30.47431562 -119.22337444\nv -7.44016598 25.84588379 -103.96392251\nv -2.38577050 -28.37970400 -110.40840313\nv 1.97261308 -9

In [399]:
source_obj_path = "test_input"
source_obj_path = "../datasets/3D_scans_per_patient_obj_files"

In [400]:
obj_list = os.listdir(source_obj_path)
obj_list

In [401]:
for obj in obj_list:
    print(os.path.join(source_obj_path, obj))
    vertices, org_mesh = gu.read_txt_obj_ls(os.path.join(source_obj_path, obj), ret_mesh=True, use_tri_mesh=False)
    print(np.mean(vertices[:, :3], axis=0))